# Sidelnikov-Shestakov's attack on Original Niederreiter

In [1]:
class Niederreiter:
    def __init__(self, F, k, M = None, P = None, pointsAlpha = None, pointsZ = None):
        self.k = k
        self.n = len(F)-1 
        self.s = self.n-1-k
        self.F = F 
        self.Flist = [i for i in self.F]
        self.Flist.remove(0)
        self.M = M
        self.P = P
        self.pointsAlpha = pointsAlpha
        self.pointsZ = pointsZ
        if self.pointsZ == None:
            self.pointsZ = []
            for i in range(self.n):
                self.pointsZ += random.sample(self.Flist, 1)
        if self.pointsAlpha == None:
            self.pointsAlpha = self.Flist
        self.GRS = codes.GeneralizedReedSolomonCode(self.pointsAlpha, k, self.pointsZ) 
        self.H = self.GRS.parity_check_matrix()
        if self.M == None:
            self.M = random_matrix(self.F,self.s+1,self.s+1)
            while self.M.is_singular():
                self.M = random_matrix(self.F,self.s+1,self.s+1)
        if self.P == None:
            self.P = Permutations(self.n).random_element().to_matrix()
        #
        self.K = self.M*self.H*self.P

## Parameters

In [2]:
import random
q = 9
F.<eta> = GF(q, name='eta', modulus=x^2 + 2*x +2 )
print("k has to be greater or equal to ", float((q-1)/2))

k has to be greater or equal to  4.0


In [3]:
k = int(input())

4


In [4]:
n = q-1
s = n-k-1

In [5]:
print("n = ", n)
print("k = ", k)
print("s = ", s)

n =  8
k =  4
s =  3


## Generate keys

In [6]:
M = matrix([[ eta + 1, 1, eta + 2, 2*eta + 1],
            [2,2,eta + 1,2*eta],
            [1,eta + 2,0,eta + 1],
            [2*eta,0,eta + 1,eta + 1]])
l = F(1)
P = matrix([[0, 0, 0, 0, 0, 0, l, 0],
           [0, 0, 0, 0, 0, l, 0, 0],
           [0, 0, 0, 0, 0, 0, 0, l],
           [0, 0, 0, l, 0, 0, 0, 0],
           [l, 0, 0, 0, 0, 0, 0, 0],
           [0, 0, 0, 0, l, 0, 0, 0],
           [0, 0, l, 0, 0, 0, 0, 0],
           [0, l, 0, 0, 0, 0, 0, 0]])
pointsAlpha = [eta, eta + 1, 2*eta + 1, 2, 2*eta, 2*eta + 2, eta + 2, 1]
pointsZ = [2*eta, 2*eta + 2, eta + 1, eta + 1, 2*eta, eta, 2, 2*eta + 2]

In [7]:
NiederreiterPKC = Niederreiter(F,k,M,P,pointsAlpha,pointsZ)
K = NiederreiterPKC.K
print("private matrix H ="),
print(NiederreiterPKC.H, "\n")
print("public matrix K ="),
print(K)

private matrix H =
[        1         1     2*eta 2*eta + 2         2       eta   eta + 2 2*eta + 2]
[      eta   eta + 1         1   eta + 1       eta   eta + 2 2*eta + 2 2*eta + 2]
[  eta + 1         2 2*eta + 1 2*eta + 2 2*eta + 2     2*eta     2*eta 2*eta + 2]
[2*eta + 1 2*eta + 2 2*eta + 2   eta + 1 2*eta + 1 2*eta + 1         2 2*eta + 2] 

public matrix K =
[  eta + 1     2*eta       eta 2*eta + 2 2*eta + 1     2*eta     2*eta         1]
[    2*eta   eta + 1 2*eta + 1       eta 2*eta + 1         1 2*eta + 2     2*eta]
[    2*eta       eta 2*eta + 1         1 2*eta + 2   eta + 2 2*eta + 2         0]
[        1     2*eta         0 2*eta + 1 2*eta + 1       eta   eta + 2         2]


## Attack

### Recover $gamma_4,...,gamma_8$

In [8]:
maxindex = min(2*s-1,n-1)

J1 = [0]+list(range(s+1,maxindex+1))
K1 = K.matrix_from_columns([i for i in J1])
c1 = K1.left_kernel().basis()[0]
pi1 = c1*K
print("c_1 = ", c1)
print("pi_1 = ", pi1)

J2 = [1]+list(range(s+1,maxindex+1))
K2 = K.matrix_from_columns([i for i in J2])
c2 = K2.left_kernel().basis()[0]
pi2 = c2*K
print("\nc_2 = ", c2)
print("pi_2 = ", pi2)

c_1 =  (0, 1, 2*eta + 2, 2*eta + 2)
pi_1 =  (0, eta + 1, 1, eta + 2, 0, 0, eta + 1, 1)

c_2 =  (1, 2*eta, 2*eta, eta + 1)
pi_2 =  (eta + 1, 0, eta + 2, 2*eta + 1, 0, 0, eta + 2, 1)


In [9]:
a1 = pi1[2] 
a2 = pi2[2]
blist = [None]*n
blist[2] = a1/a2

gammalist = list([None]*n)

for j in range(3,(s)+1):
    blist[j] = pi1[j]/pi2[j]
    gammalist[j] = blist[2]/(blist[2]-blist[j])

for j in range(2*s,(n-1)+1):
    blist[j] = pi1[j]/pi2[j]
    gammalist[j] = blist[2]/(blist[2]-blist[j])

print("(gamma_1, ..., gamma_8) = ", gammalist)

(gamma_1, ..., gamma_8) =  [None, None, None, eta + 2, None, None, 2*eta + 1, eta + 1]


In [10]:
J3 = [0]+list(range(2,(s)+1))
K3 = K.matrix_from_columns([i for i in J3])
c3 = K3.left_kernel().basis()[0]
pi3 = c3*K
print("c_3 = ", c3)
print("pi_3 = ", pi3)

J4 = [1]+list(range(2,(s)+1))
K4 = K.matrix_from_columns([i for i in J4])
c4 = K4.left_kernel().basis()[0]
pi4 = c4*K
print("\nc4 = ", c4)
print("pi_4 = ", pi4)

c_3 =  (1, eta, 1, eta)
pi_3 =  (0, eta, 0, 0, eta + 1, 2*eta, 2*eta + 2, eta)

c4 =  (1, 2*eta + 1, 2*eta, 2*eta + 1)
pi_4 =  (eta + 1, 0, 0, 0, 2*eta, eta + 2, 2, eta + 1)


In [11]:
r = random.randint(2*s,n-1)
for j in range(0,n):
    if j not in set(J3+J4+[2]):
        if gammalist[j] == None:
            blist[j] = (pi4[r]*pi3[j]*blist[r])/(pi3[r]*pi4[j])
            gammalist[j] = blist[2]/(blist[2]-blist[j]) 
print("(gamma_1, ..., gamma_8) = ", gammalist)

(gamma_1, ..., gamma_8) =  [None, None, None, eta + 2, 2*eta + 2, eta, 2*eta + 1, eta + 1]


### Transformation $\mathbb{F}_\infty^8 \to \mathbb{F}_9^8$

In [12]:
gammalist[0] = 1
gammalist[1] = 0

for i in F:
    if i not in gammalist:
        a = i
        break

betalist = gammalist[:]
for j in range(3,n):
    gammanew = 1/(a-gammalist[j])
    betalist[j] = gammanew
betalist[0] = 1/(a-1)
betalist[1] = 1/(a)
betalist[2] = 0
print("(beta_1, ..., beta_8) = ", betalist)

(beta_1, ..., beta_8) =  [1, 2, 0, 2*eta + 1, eta + 2, eta + 1, 2*eta + 2, 2*eta]


### Recover $y_1,\dots,y_5$

In [13]:
J5 = list(range(0,(s+1)+1))
K5 = K.matrix_from_columns([i for i in J5])
c5 = K5.right_kernel().basis()[0]

ylist = [None] * n
ylist[0] = 1

V = (matrix.vandermonde(betalist[:(s+1)+1]).transpose()).matrix_from_rows([i for i in range(0,s+1)])

B = V.matrix_from_columns([i for i in range(1,(s+1)+1)])
C = matrix.diagonal(c5[1:])
BC = B*C
solve = vector(-1 * c5[0] * V.matrix_from_columns([0]))
y2 = BC.solve_right(solve)

i = 1
for j in y2:
    ylist[i] = j
    i += 1
print("(y_1, ..., y_8) = ", ylist)

(y_1, ..., y_8) =  [1, eta + 1, 2*eta + 1, eta + 1, 2*eta, None, None, None]


### Recover $\hat{M}$

In [14]:
V = matrix.vandermonde(betalist[:s+1])
Mhat = [[None]*(s+1)]*(s+1)

ytmp = vector(ylist[:s+1])
yinv = vector([yi^(-1) for yi in ytmp])

for i in range(s+1):
    solve = yinv[:]
    for j in range(s+1):
        solve[j] *= K[i][j]
    Mhat[i] = V.solve_right(solve)
Mhat = matrix(Mhat)
print("\\hat{M} = ")
print(Mhat)

\hat{M} = 
[2*eta + 2     2*eta   eta + 2     2*eta]
[        1         2   eta + 1   eta + 2]
[        1     2*eta         0         2]
[        0 2*eta + 1   eta + 1         2]


### Recover $y_6, y_7, y_8$

In [15]:
Mhatinv = Mhat.inverse()
for i in range(s+2,n):
    tmpsum = 0
    for j in range(s+1):
        tmpsum += Mhatinv[0][j]*K[j][i]
    ylist[i] = tmpsum
print("(y_1, ..., y_8) = ", ylist)

(y_1, ..., y_8) =  [1, eta + 1, 2*eta + 1, eta + 1, 2*eta, 2, 2, eta]


## Check if the attack was succesful.

In [16]:
Halt = matrix.vandermonde(betalist).transpose().matrix_from_rows(list(range(0,s+1))) * matrix.diagonal(ylist)
Malt = Mhat
Kalt = Malt*Halt
if Kalt == K:
    print("Attack was succesful.")
else:
    print("Attack failed.")
    error = false
    for i in range(s+1):
        for j in range(n):
            if not Kalt[i][j] == K[i][j]:
                chyba = false
                print('Error on position', i,j)
                print(Kalt[i][j], K[i][j])

Attack was succesful.
